# Running simulations through the cloud 

This notebook is a tutorial of the API used for submitting simulations to our servers.


In [1]:
import tidy3d as td
import tidy3d.web as web

# set logging level to ERROR because we'll only running simulations to demonstrate the web API, we don't care about the results.
td.config.logging_level = "ERROR"

15:10:42 CET WARNING: Using canonical configuration directory at                
             '/home/marco/.config/tidy3d'. Found legacy directory at            
             '~/.tidy3d', which will be ignored. Remove it manually or run      
             'tidy3d config migrate --delete-legacy' to clean up.               

## Setup

Let's set up a simple simulation to get started.

In [2]:
# whether to print output in web functions, note: if False (default) they will all run silently
verbose = True

# set up parameters of simulation
dl = 0.05
pml = td.PML()
sim_size = [4, 4, 4]
freq0 = 3e14
fwidth = 1e13
run_time = 1 / fwidth

# create structure
dielectric = td.Medium.from_nk(n=2, k=0, freq=freq0)
square = td.Structure(geometry=td.Box(center=[0, 0, 0], size=[1.5, 1.5, 1.5]), medium=dielectric)

# create source
source = td.UniformCurrentSource(
    center=(-1.5, 0, 0),
    size=(0, 0.4, 0.4),
    source_time=td.GaussianPulse(freq0=freq0, fwidth=fwidth),
    polarization="Ex",
)

# create monitor
monitor = td.FieldMonitor(
    fields=["Ex", "Ey", "Ez"],
    center=(0, 0, 0),
    size=(td.inf, td.inf, 0),
    freqs=[freq0],
    name="field",
)

# Initialize simulation
sim = td.Simulation(
    size=sim_size,
    grid_spec=td.GridSpec.uniform(dl),
    structures=[square],
    sources=[source],
    monitors=[monitor],
    run_time=run_time,
    boundary_spec=td.BoundarySpec.all_sides(boundary=pml),
)

## Running simulation manually

For the most control, you can run the simulation through the Tidy3D web API.
Each simulation running on the server is identified by a `task_id`, which must be specified in the web API.
Let's walk through submitting a simulation this way.

In [3]:
# upload the simulation to our servers
task_id = web.upload(sim, task_name="webAPI", verbose=verbose)

# start the simulation running
web.start(task_id)

# monitor the simulation, don't move on to next line until completed.
web.monitor(task_id, verbose=verbose)

# download the results and load into a simulation data object for plotting, post processing etc.
sim_data = web.load(task_id, path="data/sim.hdf5", verbose=verbose)

15:10:45 CET Created task 'webAPI' with resource_id                             
             'fdve-8a9d34dd-4033-4cd9-9315-184865d379f2' and task_type 'FDTD'.

             View task using web UI at                                          
             ]8;id=811009;https://tidy3d.simulation.cloud/workbench?taskId=fdve-8a9d34dd-4033-4cd9-9315-184865d379f2\'https://tidy3d.simulation.cloud/workbench?]8;;\]8;id=292393;https://tidy3d.simulation.cloud/workbench?taskId=fdve-8a9d34dd-4033-4cd9-9315-184865d379f2\taskId]8;;\]8;id=811009;https://tidy3d.simulation.cloud/workbench?taskId=fdve-8a9d34dd-4033-4cd9-9315-184865d379f2\=]8;;\]8;id=246506;https://tidy3d.simulation.cloud/workbench?taskId=fdve-8a9d34dd-4033-4cd9-9315-184865d379f2\fdve]8;;\]8;id=811009;https://tidy3d.simulation.cloud/workbench?taskId=fdve-8a9d34dd-4033-4cd9-9315-184865d379f2\-8a9d34dd-403]8;;\
             ]8;id=811009;https://tidy3d.simulation.cloud/workbench?taskId=fdve-8a9d34dd-4033-4cd9-9315-184865d379f2\3-4cd9-9315-184865d379f2']8;;\.

             Task folder: ]8;id=154002;https://tidy3d.simulation.cloud/folders/folder-df61810d-cad6-4474-8ea9-e4f00d5dfcb0\'default']8;;\.

Output()

15:10:48 CET Estimated FlexCredit cost: 0.025. Minimum cost depends on task     
             execution details. Use 'web.real_cost(task_id)' to get the billed  
             FlexCredit cost after a simulation run.

...

Output()

15:15:00 CET status = success

             View simulation result at                                          
             ]8;id=673546;https://tidy3d.simulation.cloud/workbench?taskId=fdve-8a9d34dd-4033-4cd9-9315-184865d379f2\'https://tidy3d.simulation.cloud/workbench?]8;;\]8;id=12410;https://tidy3d.simulation.cloud/workbench?taskId=fdve-8a9d34dd-4033-4cd9-9315-184865d379f2\taskId]8;;\]8;id=673546;https://tidy3d.simulation.cloud/workbench?taskId=fdve-8a9d34dd-4033-4cd9-9315-184865d379f2\=]8;;\]8;id=351622;https://tidy3d.simulation.cloud/workbench?taskId=fdve-8a9d34dd-4033-4cd9-9315-184865d379f2\fdve]8;;\]8;id=673546;https://tidy3d.simulation.cloud/workbench?taskId=fdve-8a9d34dd-4033-4cd9-9315-184865d379f2\-8a9d34dd-403]8;;\
             ]8;id=673546;https://tidy3d.simulation.cloud/workbench?taskId=fdve-8a9d34dd-4033-4cd9-9315-184865d379f2\3-4cd9-9315-184865d379f2']8;;\.

Output()

15:15:06 CET Loading simulation from data/sim.hdf5

While we broke down each of the individual steps above, one can also perform the entire process in one line by calling the [web.run()](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.web.api.run.run.html) function as follows.

```python
sim_data = web.run(sim, task_name='webAPI', path='data/sim.hdf5')
```

(We won't run it again in this notebook to save time).

Sometimes this is more convenient, but other times it can be helpful to have the steps broken down one by one, for example if the simulation is long, you may want to [web.start](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.web.api.webapi.start.html) and then exit the session and load the results at a later time using [web.load](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.web.api.webapi.load.html).


## Job Container

The [web.Job](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.web.api.container.Job.html) interface provides a more convenient way to manage single simulations, mainly because it eliminates the need for keeping track of the `task_id` and original [Simulation](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.Simulation.html).

We can get the cost estimate of running the task before actually running it. This prevents us from accidentally running large jobs that we set up by mistake. The estimated cost is the maximum cost corresponding to running all the time steps.

In [4]:
# initializes job, puts task on server (but doesn't run it)
job = web.Job(simulation=sim, task_name="job", verbose=verbose)

# estimate the maximum cost
estimated_cost = web.estimate_cost(job.task_id)

             Created task 'job' with resource_id                                
             'fdve-d6c5317b-6b06-4d8c-8b0b-0cbf102494d6' and task_type 'FDTD'.

             View task using web UI at                                          
             ]8;id=589602;https://tidy3d.simulation.cloud/workbench?taskId=fdve-d6c5317b-6b06-4d8c-8b0b-0cbf102494d6\'https://tidy3d.simulation.cloud/workbench?]8;;\]8;id=350894;https://tidy3d.simulation.cloud/workbench?taskId=fdve-d6c5317b-6b06-4d8c-8b0b-0cbf102494d6\taskId]8;;\]8;id=589602;https://tidy3d.simulation.cloud/workbench?taskId=fdve-d6c5317b-6b06-4d8c-8b0b-0cbf102494d6\=]8;;\]8;id=335527;https://tidy3d.simulation.cloud/workbench?taskId=fdve-d6c5317b-6b06-4d8c-8b0b-0cbf102494d6\fdve]8;;\]8;id=589602;https://tidy3d.simulation.cloud/workbench?taskId=fdve-d6c5317b-6b06-4d8c-8b0b-0cbf102494d6\-d6c5317b-6b0]8;;\
             ]8;id=589602;https://tidy3d.simulation.cloud/workbench?taskId=fdve-d6c5317b-6b06-4d8c-8b0b-0cbf102494d6\6-4d8c-8b0b-0cbf102494d6']8;;\.

             Task folder: ]8;id=284749;https://tidy3d.simulation.cloud/folders/folder-df61810d-cad6-4474-8ea9-e4f00d5dfcb0\'default']8;;\.

Output()

15:15:09 CET Estimated FlexCredit cost: 0.025. Minimum cost depends on task     
             execution details. Use 'web.real_cost(task_id)' to get the billed  
             FlexCredit cost after a simulation run.

15:15:11 CET Estimated FlexCredit cost: 0.025. Minimum cost depends on task     
             execution details. Use 'web.real_cost(task_id)' to get the billed  
             FlexCredit cost after a simulation run.

While [Job](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.web.api.container.Job.html) has methods with names identical to the web API functions above, which give some more granular control, it is often most convenient to call `.run()` so we will do that now.

In [5]:
# start job, monitor, and load results
sim_data = job.run(path="data/sim.hdf5")

15:15:15 CET status = success

Output()

15:15:18 CET Loading simulation from data/sim.hdf5

Another convenient thing about [Job](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.web.api.container.Job.html) objects is that they can be saved and loaded just like other Tidy3d components.

This is convenient if you want to save and load up the results of a job that has already finished, without needing to know the `task_id`.

In [6]:
# saves the job metadata to a single file
job.to_file("data/job.json")

# can exit session, break here, or continue in new session.

# load the job metadata from file
job_loaded = web.Job.from_file("data/job.json")

# download the data from the server and load it into a SimulationData object.
sim_data = job_loaded.load(path="data/sim.hdf5")

Output()

15:15:21 CET Loading simulation from data/sim.hdf5

## Batch Processing

Commonly one needs to submit a batch of Simulations.
One way to approach this using the web API is to upload, start, monitor, and load a series of tasks one by one, but this is clumsy and you can lose your data if the session gets interrupted.

A better way is to use the built-in [Batch](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.web.api.container.Batch.html) object.
The batch object is like a [Job](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.web.api.container.Job.html), but stores task metadata for a series of simulations.

In [7]:
# make a dictionary of  {task name : simulation} for demonstration
sims = {f"sim_{i}": sim for i in range(3)}

# initialize a batch and run them all
batch = web.Batch(simulations=sims, verbose=verbose)

# run the batch and store all of the data in the `data/` dir.
batch_results = batch.run(path_dir="data")

Output()

15:15:26 CET Started working on Batch containing 3 tasks.

15:15:33 CET Maximum FlexCredit cost: 0.075 for the whole batch.

             Use 'Batch.real_cost()' to get the billed FlexCredit cost after    
             completion.

Output()

15:15:48 CET Batch complete.

When the batch is completed, the output is not a [SimulationData](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.SimulationData.html) but rather a [BatchData](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.web.api.container.BatchData.html).  The data within this [BatchData](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.web.api.container.BatchData.html) object can either be indexed directly `batch_results[task_name]` or can be looped through `batch_results.items()` to get the [SimulationData](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.SimulationData.html) for each task.

This was chosen to reduce the memory strain from loading all [SimulationData](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.SimulationData.html) objects at once.

Alternatively, the batch can be looped through (several times) using the `.items()` method, similar to a dictionary.

In [8]:
# grab the sum of intensities in the simulation one by one (to save memory)
intensities = {}
for task_name, sim_data in batch_results.items():
    intensity = sim_data.get_intensity("field").sel(f=freq0)
    sum_intensity = float(intensity.sum(("x", "y")).values[0])
    intensities[task_name] = sum_intensity

print(intensities)

15:15:55 CET Loading simulation from                                            
             data/fdve-ef73aa96-65f9-4793-9b1d-26ea9b39c6b2.hdf5

15:15:56 CET Loading simulation from                                            
             data/fdve-c229e1b2-0bb8-44df-a570-df73ab419ba8.hdf5

15:16:00 CET Loading simulation from                                            
             data/fdve-2cd0c62f-c207-4191-b057-f2a1c753aed1.hdf5

{'sim_0': 6473211.0, 'sim_1': 6473211.0, 'sim_2': 6473211.0}


## Simulation Batching

Finally, one perform batch processing of several simulations in a single function call.

For this purpose, [web.run](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.web.api.run.run.html) function can also be used for any nested combinations of dictionaries, lists or tuples.

Here is the previous example repeated using this feature.

In [9]:
batch_results_dict = web.run(sims, verbose=verbose)
# sim_list = list(sims.values())
# batch_results_list = web.run(sim_list, verbose=verbose) # this would return a plain list of SimulationData

15:16:01 CET Created task 'fdtd_2025-10-29_15-16-00' with resource_id           
             'fdve-0e9a1dac-0a3c-431d-af51-3e63bc484aa2' and task_type 'FDTD'.

             View task using web UI at                                          
             ]8;id=655135;https://tidy3d.simulation.cloud/workbench?taskId=fdve-0e9a1dac-0a3c-431d-af51-3e63bc484aa2\'https://tidy3d.simulation.cloud/workbench?]8;;\]8;id=710211;https://tidy3d.simulation.cloud/workbench?taskId=fdve-0e9a1dac-0a3c-431d-af51-3e63bc484aa2\taskId]8;;\]8;id=655135;https://tidy3d.simulation.cloud/workbench?taskId=fdve-0e9a1dac-0a3c-431d-af51-3e63bc484aa2\=]8;;\]8;id=170182;https://tidy3d.simulation.cloud/workbench?taskId=fdve-0e9a1dac-0a3c-431d-af51-3e63bc484aa2\fdve]8;;\]8;id=655135;https://tidy3d.simulation.cloud/workbench?taskId=fdve-0e9a1dac-0a3c-431d-af51-3e63bc484aa2\-0e9a1dac-0a3]8;;\
             ]8;id=655135;https://tidy3d.simulation.cloud/workbench?taskId=fdve-0e9a1dac-0a3c-431d-af51-3e63bc484aa2\c-431d-af51-3e63bc484aa2']8;;\.

             Task folder: ]8;id=515771;https://tidy3d.simulation.cloud/folders/folder-df61810d-cad6-4474-8ea9-e4f00d5dfcb0\'default']8;;\.

Output()

15:16:06 CET Estimated FlexCredit cost: 0.025. Minimum cost depends on task     
             execution details. Use 'web.real_cost(task_id)' to get the billed  
             FlexCredit cost after a simulation run.

15:16:09 CET status = success

Output()

15:16:20 CET Loading simulation from simulation_data.hdf5

In [10]:
# grab the sum of intensities in the simulation one by one (to save memory)
intensities = {}
for task_name, sim_data in batch_results_dict.items():
    intensity = sim_data.get_intensity("field").sel(f=freq0)
    sum_intensity = float(intensity.sum(("x", "y")).values[0])
    intensities[task_name] = sum_intensity

print(intensities)

{'sim_0': 6473211.0, 'sim_1': 6473211.0, 'sim_2': 6473211.0}


After going through this tutorial, you have learned how to run simulations with Tidy3D via the web API. If you are new to Tidy3D or the finite-difference time-domain (FDTD) method, we highly recommend going through our [FDTD101](https://www.flexcompute.com/fdtd101/) tutorials and [example library](https://www.flexcompute.com/tidy3d/examples/) before starting your own simulation adventure. 